# First pipeline steps
## Pipline to clean, join, filter, and check sequences before OTU picking/clustering

## Setup (run these each time you restart notebook)

In [1]:
from IPython.display import FileLinks, FileLink

# Setting up variables

## Specific variables that should not change

In [1]:
%env REF=/home/sam/data/databases/silva
%env TMPDIR=/home/sam/data/databases/silva/tmp
%env TRIMMOMATIC=/home/sam//programs/Trimmomatic-0.39/trimmomatic-0.39.jar

import os
ref = os.getenv("REF")

env: REF=/home/sam/data/databases/silva
env: TMPDIR=/home/sam/data/databases/silva/tmp
env: TRIMMOMATIC=/home/sam//programs/Trimmomatic-0.39/trimmomatic-0.39.jar


## Setting up run specific variables

In [2]:
base = "/home/sam/data/databases/silva"

'base' is the main folder that will contain the analysis

'RAW' will contain the original sequencing files (fastq.gz)

'TRIM_OUT' contains the trimmed fastq files

'PANDA_OUT' contains the joined/merged fasta files

'FILTER_OUT' contains the filtered fasta files with renamed sequences

'CONVERT_OUT' contains the input for QIIME 2

'CHIMERA_OUT' contains the chimera checked sequences

'CLUSTER_OUT' contains the clustered OTU output

In [3]:
%env BASE=$base
%env RAW=$base/raw
%env TRIM_OUT=$base/trimmed
%env PANDA_OUT=$base/joined
%env FILTER_OUT=$base/filtered
%env CONVERT_OUT=$base/converted
%env CHIMERA_OUT=$base/chimera_checked
%env CLUSTER_OUT=$base/clustered
%env CLASSIFY_OUT=$base/classified

# Specific to clustering
%env CLUSTER_PER=99
%env MYREF=$ref/ref-seqs-silva-138-99-seqs.qza
%env MYREF2=$ref/SILVA-138.1-full-length-seq-taxonomy-with_species.qza
%env MYREF3=$ref/ref-seqs-gg_13_8-99_otus.qza

# Specific to classifying
%env REFSEQ=$ref/

env: BASE=/home/sam/data/databases/silva
env: RAW=/home/sam/data/databases/silva/raw
env: TRIM_OUT=/home/sam/data/databases/silva/trimmed
env: PANDA_OUT=/home/sam/data/databases/silva/joined
env: FILTER_OUT=/home/sam/data/databases/silva/filtered
env: CONVERT_OUT=/home/sam/data/databases/silva/converted
env: CHIMERA_OUT=/home/sam/data/databases/silva/chimera_checked
env: CLUSTER_OUT=/home/sam/data/databases/silva/clustered
env: CLASSIFY_OUT=/home/sam/data/databases/silva/classified
env: CLUSTER_PER=97
env: MYREF=/home/sam/data/databases/silva/ref-seqs-silva-138-99-seqs.qza
env: MYREF2=/home/sam/data/databases/silva/SILVA-138.1-full-length-seq-taxonomy-with_species.qza
env: MYREF3=/home/sam/data/databases/silva/ref-seqs-gg_13_8-99_otus.qza
env: REFSEQ=/home/sam/data/databases/silva/


## Get list of samples

In [4]:
%%bash

if [[ -e ${BASE}/sample_ids.txt ]]; then
    rm ${BASE}/sample_ids.txt
fi

for file in ${RAW}/*R1*
do
    NAME=$(echo ${file} | awk -F "/" '{print $NF}' | awk -F ".R1" '{print $1}')
    echo ${NAME}
    echo ${NAME} >> ${BASE}/sample_ids.txt
done

SAMPLE_COUNT=$(wc ${BASE}/sample_ids.txt | awk '{print $1}')
echo -e "\nSample Count = ${SAMPLE_COUNT}"

Mock-Community-Pos-Control_S55_L001

Sample Count = 1


## Trimming - Trimmomatic
Trimmomatic Steps
1. Remove adapters
2. Remove leading/trailing low quality bases (quality score if 3 or lower, remove sequence)
3. Sliding window quality trimming (window of size 8 with average quality score of 10, remove if below)
4. Removing short reads (if length < 100)


Output:
- NAME.trimmed.paired.R1 : Sample trimmed paired R1 reads
- NAME.trimmed.paired.R2 : Sample trimmed paired R2 reads
- NAME.trimmed.unpaired.R1 : Sample trimmed broken R1 reads
- NAME.trimmed.unpaired.R2 : Sample trimmed broken R2 reads
- NAME.trimmomatic.log : Per sequence trimming information
- NAME.trimmomatic.stats.txt : Trimming stats for sample

In [7]:
%%bash

if [ ! -d ${TRIM_OUT} ]; then
    mkdir ${TRIM_OUT}
fi

for NAME in $(cat ${BASE}/sample_ids.txt)
do
    java -jar ${TRIMMOMATIC} \
        PE -phred33 \
        -threads 8 \
        -trimlog ${TRIM_OUT}/${NAME}.trimmomatic.log \
        ${RAW}/${NAME}_R1_001.fastq \
        ${RAW}/${NAME}_R2_001.fastq \
        ${TRIM_OUT}/${NAME}.trimmed.paired.R1.fq \
        ${TRIM_OUT}/${NAME}.trimmed.unpaired.R1.fq \
        ${TRIM_OUT}/${NAME}.trimmed.paired.R2.fq \
        ${TRIM_OUT}/${NAME}.trimmed.unpaired.R2.fq \
        LEADING:3 \
        TRAILING:3 \
        SLIDINGWINDOW:8:10 \
        MINLEN:100 \
        > ${TRIM_OUT}/${NAME}.trimmomatic.stats.txt 2>&1
done


## List the samples that passed trimming

In [8]:
%%bash

# Generate list of sample ids that passed trimming
if [ -f ${BASE}/sample_ids.pass_trimmed.txt ]; then
    rm ${BASE}/sample_ids.pass_trimmed.txt
fi

for file in $(ls -1 ${TRIM_OUT}/*trimmed.paired.R1.fq)
do
    NAME=$(echo ${file} | awk -F "/" '{print $NF}' | awk -F ".trimmed" '{print $1}')
    echo ${NAME}
    echo ${NAME} >> ${BASE}/sample_ids.pass_trimmed.txt
done

SAMPLE_COUNT=$(wc ${BASE}/sample_ids.pass_trimmed.txt | awk '{print $1}')
echo -e "\nSample Count = ${SAMPLE_COUNT}"

Mock-Community-Pos-Control_S55_L001

Sample Count = 1


## Joining - pandaseq

Output:
- NAME.joined.fa : Sample joined sequence fasta file
- NAME.joined.lengths.txt : Lengths of the sequences from the fasta file
- NAME.pandaseq.log : Log file from pandaseq

In [12]:
%%bash
ls

1 Trim_Join_Cluster_Chimera_Class.ipynb
gg_13_8-99_otus.fasta.qza
gg_13_8-99_otus_taxonomy.qza
gg_13_8_otus
gg_13_8_otus.tar
ids_to_keep-no_species.txt
ids_to_keep-with_species.txt
joined
qiime2-testing.ipynb
raw
ref-seqs-gg_13_8-99_otus.qza
ref-seqs-silva-138-99-seqs.qza
sample_ids.pass_joined.txt
sample_ids.pass_trimmed.txt
sample_ids.txt
seq_dist.pl
seq_rename_and_filter.pl
seq_stats.R
SILVA-138.1-full-length-seq-taxonomy-no_species.qza
SILVA-138.1-full-length-seq-taxonomy-with_species.qza
SILVA-138.1-SSURef-full-length-classifier-no_species.qza
SILVA-138.1-SSURef-full-length-classifier-with_species.qza
SILVA-138.1-SSURef-Full-Seqs-no_species.qza
SILVA-138.1-SSURef-Full-Seqs-with_species.qza
SILVA_138.1_SSURef_NR99_tax_silva.fasta
SILVA_138.1_SSURef_NR99_tax_silva_full_align_trunc.fasta
SILVA_138.1_SSURef_NR99_tax_silva_trunc.fasta
SILVA-138.1-Taxonomy-no_species.txt
SILVA-138.1-Taxonomy-with_species.txt
silva-138-99-seqs.qza
SILVA_align_seqs.fasta
SILVA_align_seqs_polyfilt_lenfilt-

In [14]:
%%bash

if [ ! -d ${PANDA_OUT} ]; then
    mkdir ${PANDA_OUT}
fi

for NAME in $(cat ${BASE}/sample_ids.pass_trimmed.txt)
do
    pandaseq \
        -T 8 \
        -g ${PANDA_OUT}/${NAME}.pandaseq.log \
        -f ${TRIM_OUT}/${NAME}.trimmed.paired.R1.fq \
        -r ${TRIM_OUT}/${NAME}.trimmed.paired.R2.fq \
        -w ${PANDA_OUT}/${NAME}.joined.fa

    ./seq_dist.pl \
        ${PANDA_OUT}/${NAME}.joined.fa \
        > ${PANDA_OUT}/${NAME}.joined.lengths.txt
done

In [15]:
%%bash

# Generate list of samples that passed the joining step
if [ -f ${BASE}/sample_ids.pass_joined.txt ]; then
    rm ${BASE}/sample_ids.pass_joined.txt
fi

for file in $(ls -1 ${PANDA_OUT}/*joined.fa)
do
    NAME=$(echo ${file} | awk -F "/" '{print $NF}' | awk -F ".joined" '{print $1}')
    echo ${NAME}
    echo ${NAME} >> ${BASE}/sample_ids.pass_joined.txt
done

SAMPLE_COUNT=$(wc ${BASE}/sample_ids.pass_joined.txt | awk '{print $1}')
echo -e "\nSample Count = ${SAMPLE_COUNT}"

Mock-Community-Pos-Control_S55_L001

Sample Count = 1


# Stats for each sample after joining

In [16]:
%%bash

# Run the R script to generate the stats
./seq_stats.R ${PANDA_OUT}

                                     X1  X2  X3       X4  X5  X6
Mock-Community-Pos-Control_S55_L001 133 292 292 292.4641 292 500


# Filtering and renaming sequences

- Filtering
- Removing if
  - 7 or more N's
  - Homopolymers greater then 7 in length
  - Sequence length less than 400
  
  
- Need to rename the sequences to contain the sample ID

In [17]:
%%bash

# Setup the filter output folder
if [ ! -d ${FILTER_OUT} ]; then
    mkdir ${FILTER_OUT}
fi

# Loop through the samples and filter the fasta files
for NAME in $(cat ${BASE}/sample_ids.pass_joined.txt)
do
    ./seq_rename_and_filter.pl \
        ${PANDA_OUT}/${NAME}.joined.fa \
        ${NAME} \
        7 7 400 \
        > ${FILTER_OUT}/${NAME}.filtered.fa
done

In [18]:
%%bash

# Generate list of samples that passed the filtering step
if [ -f ${BASE}/sample_ids.pass_filtered.txt ]; then
    rm ${BASE}/sample_ids.pass_filtered.txt
fi

for file in $(ls -1 ${FILTER_OUT}/*.filtered.fa)
do
    NAME=$(echo ${file} | awk -F "/" '{print $NF}' | awk -F ".filtered" '{print $1}')
    echo ${NAME}
    echo ${NAME} >> ${BASE}/sample_ids.pass_filtered.txt
done

SAMPLE_COUNT=$(wc ${BASE}/sample_ids.pass_filtered.txt | awk '{print $1}')
echo -e "\nSample Count = ${SAMPLE_COUNT}"

Mock-Community-Pos-Control_S55_L001

Sample Count = 1


# Start of QIIME 2 Stuff
## Import fasta file into QIIME2 as a qza file

In [19]:
%%bash

if [ ! -d ${CONVERT_OUT} ]; then
    mkdir ${CONVERT_OUT}
fi

# Merge the filtered fasta files into a single file for import
cat ${FILTER_OUT}/*filtered.fa >> ${CONVERT_OUT}/all.sequences.filtered.fa

qiime \
    tools import \
    --input-path ${CONVERT_OUT}/all.sequences.filtered.fa \
    --output-path ${CONVERT_OUT}/all.sequences.filtered.qza \
    --type 'SampleData[Sequences]' \

Imported /home/sam/data/databases/silva/converted/all.sequences.filtered.fa as QIIME1DemuxDirFmt to /home/sam/data/databases/silva/converted/all.sequences.filtered.qza


## Dereplicate the qza file to generate the frequency table qza file

In [20]:
%%bash

qiime \
    vsearch dereplicate-sequences \
    --i-sequences ${CONVERT_OUT}/all.sequences.filtered.qza \
    --o-dereplicated-table ${CONVERT_OUT}/rep-seqs.table.qza \
    --o-dereplicated-sequences ${CONVERT_OUT}/rep-seqs.qza

Saved FeatureTable[Frequency] to: /home/sam/data/databases/silva/converted/rep-seqs.table.qza
Saved FeatureData[Sequence] to: /home/sam/data/databases/silva/converted/rep-seqs.qza


# Create reference file for clustering
## This is for a 97% clustered file from Silva_132 release
## SKIP THIS STEP IF THE REFERENCE FILE ALREADY EXISTS

This creates a Silva 132 97% reference file

In [20]:
%%bash

qiime tools import \
    --input-path /home/linda.rhodes/qiime/references/silva_132_97_16S.fna \
    --output-path /home/linda.rhodes/qiime/references/silva_132_97_16S.qza \
    --type FeatureData[Sequence]

This creates a Greengenes 13_8 97% reference file

In [20]:
%%bash

qiime tools import \
    --input-path /home/linda.rhodes/qiime/references/97_otus.fasta \
    --output-path /home/linda.rhodes/qiime/references/gg_13_8_otus.qza \
    --type FeatureData[Sequence]

## OTU Clustering: either use open reference or closed reference.
## Both options are listed below

## Clustering with open reference                                               (MYREF=Silva 132; MYREF2=Greengenes)
## This is done in a tmp folder on data2 due to space demands

In [21]:
%%bash

if [ ! -d ${CLUSTER_OUT} ]; then
    mkdir ${CLUSTER_OUT}
fi

echo $TMPDIR

qiime \
    vsearch cluster-features-open-reference \
    --i-table ${CONVERT_OUT}/rep-seqs.table.qza \
    --i-sequences ${CONVERT_OUT}/rep-seqs.qza \
    --i-reference-sequences ${MYREF} \
    --p-perc-identity 0.${CLUSTER_PER} \
    --o-clustered-table ${CLUSTER_OUT}/table-or-${CLUSTER_PER}.qza \
    --o-clustered-sequences ${CLUSTER_OUT}/rep-seqs-or-${CLUSTER_PER}.qza \
    --o-new-reference-sequences ${CLUSTER_OUT}/new-ref-seqs-or-${CLUSTER_PER}.qza \
    --p-threads 0

/home/sam/data/databases/silva/tmp
Saved FeatureTable[Frequency] to: /home/sam/data/databases/silva/clustered/table-or-97.qza
Saved FeatureData[Sequence] to: /home/sam/data/databases/silva/clustered/rep-seqs-or-97.qza
Saved FeatureData[Sequence] to: /home/sam/data/databases/silva/clustered/new-ref-seqs-or-97.qza


## Clustering with closed reference (MYREF=Silva 132; MYREF2=Greengenes), ran Nov 2018
## This is done in a tmp folder on data2 due to space demands

In [28]:
%%bash

if [ ! -d ${CLUSTER_OUT} ]; then
    mkdir ${CLUSTER_OUT}
fi

echo $TMPDIR

qiime \
    vsearch cluster-features-closed-reference \
    --i-table ${CONVERT_OUT}/rep-seqs.table.qza \
    --i-sequences ${CONVERT_OUT}/rep-seqs.qza \
    --i-reference-sequences ${MYREF3} \
    --p-perc-identity 0.${CLUSTER_PER} \
    --o-clustered-table ${CLUSTER_OUT}/table-cr-${CLUSTER_PER}.qza \
    --o-clustered-sequences ${CLUSTER_OUT}/rep-seqs-cr-${CLUSTER_PER}.qza \
    --o-unmatched-sequences ${CLUSTER_OUT}/unmatched-ref-seqs-cr-${CLUSTER_PER}.qza \
    --p-threads 0

/home/sam/data/databases/silva/tmp


Plugin error from vsearch:

  No matches were identified to reference_sequences. This can happen if sequences are not homologous to reference_sequences, or if sequences are not in the same orientation as reference_sequences (i.e., if sequences are reverse complemented with respect to reference sequences). Sequence orientation can be adjusted with the strand parameter.

Debug info has been saved to /tmp/qiime2-q2cli-err-mrn7hoi9.log


CalledProcessError: Command 'b'\nif [ ! -d ${CLUSTER_OUT} ]; then\n    mkdir ${CLUSTER_OUT}\nfi\n\necho $TMPDIR\n\nqiime \\\n    vsearch cluster-features-closed-reference \\\n    --i-table ${CONVERT_OUT}/rep-seqs.table.qza \\\n    --i-sequences ${CONVERT_OUT}/rep-seqs.qza \\\n    --i-reference-sequences ${MYREF3} \\\n    --p-perc-identity 0.${CLUSTER_PER} \\\n    --o-clustered-table ${CLUSTER_OUT}/table-cr-${CLUSTER_PER}.qza \\\n    --o-clustered-sequences ${CLUSTER_OUT}/rep-seqs-cr-${CLUSTER_PER}.qza \\\n    --o-unmatched-sequences ${CLUSTER_OUT}/unmatched-ref-seqs-cr-${CLUSTER_PER}.qza \\\n    --p-threads 0\n'' returned non-zero exit status 1.

## Chimera Check:  this is done in a tmp folder on data2 due to space demands 

In [23]:
%%bash

if [ ! -d ${CHIMERA_OUT} ]; then
    mkdir ${CHIMERA_OUT}
fi

echo $TMPDIR

qiime \
    vsearch uchime-denovo \
    --i-table ${CLUSTER_OUT}/table-or-${CLUSTER_PER}.qza \
    --i-sequences ${CLUSTER_OUT}/rep-seqs-or-${CLUSTER_PER}.qza \
    --o-chimeras ${CHIMERA_OUT}/chimeras.qza \
    --o-nonchimeras ${CHIMERA_OUT}/nonchimeras.qza \
    --o-stats ${CHIMERA_OUT}/chimera-check-stats.qza

/home/sam/data/databases/silva/tmp
Saved FeatureData[Sequence] to: /home/sam/data/databases/silva/chimera_checked/chimeras.qza
Saved FeatureData[Sequence] to: /home/sam/data/databases/silva/chimera_checked/nonchimeras.qza
Saved UchimeStats to: /home/sam/data/databases/silva/chimera_checked/chimera-check-stats.qza


## Use the non-chimeric sequences to exlude chimeras & borderline sequences from the clustered table & sequence files

In [24]:
%%bash

qiime \
    feature-table filter-features \
    --i-table ${CLUSTER_OUT}/table-or-${CLUSTER_PER}.qza \
    --m-metadata-file ${CHIMERA_OUT}/nonchimeras.qza \
    --o-filtered-table ${CHIMERA_OUT}/table-nonchimeric-wo-borderline.qza

qiime \
    feature-table filter-seqs \
    --i-data ${CLUSTER_OUT}/rep-seqs-or-${CLUSTER_PER}.qza \
    --m-metadata-file ${CHIMERA_OUT}/nonchimeras.qza \
    --o-filtered-data ${CHIMERA_OUT}/rep-seqs-nonchimeric-wo-borderline.qza

qiime \
    feature-table summarize \
    --i-table ${CHIMERA_OUT}/table-nonchimeric-wo-borderline.qza \
    --o-visualization ${CHIMERA_OUT}/table-nonchimeric-wo-borderline.qzv

Saved FeatureTable[Frequency] to: /home/sam/data/databases/silva/chimera_checked/table-nonchimeric-wo-borderline.qza
Saved FeatureData[Sequence] to: /home/sam/data/databases/silva/chimera_checked/rep-seqs-nonchimeric-wo-borderline.qza
Saved Visualization to: /home/sam/data/databases/silva/chimera_checked/table-nonchimeric-wo-borderline.qzv


## Examine chimera filtering statistics

In [25]:
%%bash

qiime metadata tabulate \
  --m-input-file ${CHIMERA_OUT}/chimera-check-stats.qza \
  --o-visualization ${CHIMERA_OUT}/chimera-check-stats.qzv

Saved Visualization to: /home/sam/data/databases/silva/chimera_checked/chimera-check-stats.qzv


## Classify OTUs with VSEARCH consensus classifier using Silva 132 reference file
## This is done in a tmp folder on data2 due to space demands

In [27]:
%%bash

if [ ! -d ${CLASSIFY_OUT} ]; then
    mkdir ${CLASSIFY_OUT}
fi

echo $TMPDIR

qiime feature-classifier classify-consensus-vsearch \
    --i-query ${CHIMERA_OUT}/nonchimeras.qza \
    --i-reference-reads ${REFSEQ}/ref-seqs-silva-138-99-seqs.qza \
    --i-reference-taxonomy ${REFSEQ}/SILVA-138.1-full-length-seq-taxonomy-with_species.qza \
    --p-maxaccepts 10 \
    --p-perc-identity 0.8 \
    --p-strand "both" \
    --p-min-consensus 0.51 \
    --p-threads 8 \
    --o-classification ${CLASSIFY_OUT}/rep-seqs-classified-by-Silva.qza \
    --output-dir ${CLASSIFY_OUT}/rep-seqs-unspecified-by-Silva.qza

/home/sam/data/databases/silva/tmp
Saved FeatureData[Taxonomy] to: /home/sam/data/databases/silva/classified/rep-seqs-classified-by-Silva.qza
